# 0. 기본 정보
* 코드 작성자: 여서연
* 코드 작성일: 2024-05-21
* 데이터 분석 목적: 지도 시각화 적합성 확인

# 1. 기초 설정

## 사용 라이브러리

In [1]:
import pandas as pd
import folium
from pyproj import Transformer

import warnings
warnings.filterwarnings('ignore')

# 2. 전처리

In [2]:
df = pd.read_csv('../data/서울시 폐수배출시설 공간정보.csv', encoding='cp949')

In [3]:
df.sample(5)

허가신고번호  소재지_지번_법정동  소재지_지번_산 소재지_지번_번지  소재지_지번_호  \
7820  316000022200200019  1153010700       1.0       122      16.0   
9799  320000022200300036  1162010100       1.0      1659       1.0   
2315  301000022200100004  1114013200       1.0        12       1.0   
443   300000022200100113  1111015100       1.0       121       NaN   
3523  302000022199800217  1117011600       1.0       168      36.0   

                          소재지_지번_통주소               대표업종명 휴폐업구분   구명  \
7820         서울특별시 구로구 개봉동 122-16 번지               일반 의원   NaN  구로구   
9799          서울특별시 관악구 봉천동 1659-1번지             자동차 세차업   제외사  관악구   
2315  서울특별시 중구 충무로4가 12-1번지 일진빌딩316호                 NaN    폐쇄   중구   
443     서울특별시 종로구 묘동 121번지 근완빌딩 501호  귀금속 장신구 및 관련제품 제조업    폐업  종로구   
3523    서울특별시 용산구 청암동 168-36번지 외3필지지             주유소 운영업   NaN  용산구   

                X좌표            Y좌표  
7820  186499.196822  444780.297619  
9799  196673.146098  441972.021633  
2315  199473.606434  451467.699324  
443   199246.665989  452665.814615  
3523  195216.270296  448384.006599

In [4]:
# 결측치 확인
df.isnull().sum()

허가신고번호           0
소재지_지번_법정동       0
소재지_지번_산       691
소재지_지번_번지        0
소재지_지번_호      2594
소재지_지번_통주소       0
대표업종명         4946
휴폐업구분         4456
구명               0
X좌표              0
Y좌표              0
dtype: int64

## 현재 영업 중인 곳만 추출

In [5]:
df['휴폐업구분'].unique()

array([nan, '폐업', '폐쇄', '제외사', '재개업', '휴업'], dtype=object)

* 제외사? by ChatGPT
---
'제외사'는 주로 사업체 데이터에서 사용되는 용어로, 특정 조건에 의해 분석 대상에서 제외된 사업체를 의미합니다. 이는 다음과 같은 이유로 분석 대상에서 제외될 수 있습니다:

1. **자료 수집 오류**: 데이터 수집 과정에서 발생한 오류로 인해 잘못된 정보가 포함된 경우.
2. **기준 미달**: 분석 기준에 맞지 않거나, 조사 시점에서 영업을 하지 않는 등 기준에 부합하지 않는 경우.
3. **중복 기록**: 동일한 사업체가 중복으로 기록된 경우, 하나의 기록만 유지하고 나머지를 제외할 때.
4. **특정 조건에 의한 제외**: 특정 연구나 분석에서 필요하지 않은 사업체를 제외하는 경우. 예를 들어, 특정 업종이나 지역에 대한 연구에서 해당하지 않는 업종이나 지역의 사업체를 제외하는 경우.

따라서 '제외사'로 표시된 데이터는 분석의 정확성을 위해 의도적으로 제외된 경우를 나타내며, 실제 영업 상태와는 관계가 없을 수 있습니다. 이러한 항목은 데이터 정제 과정에서 제거되어 분석 대상에서 빠지게 됩니다.

In [6]:
df_work = df[df['휴폐업구분'].isna() | (df['휴폐업구분'] == '재개업')]
df_work['휴폐업구분'].unique()

array([nan, '재개업'], dtype=object)

# 3. 지도 시각화

## 좌표계 변환

In [7]:
# EPSG:5181 -> EPSG:4326(WGS84) 변환기 설정
transformer = Transformer.from_crs("epsg:5181", "epsg:4326", always_xy=True)

# 좌표 변환 함수
def transform_coords(row):
    lon, lat = transformer.transform(row['X좌표'], row['Y좌표'])
    return pd.Series([lat, lon])

# 새로운 열 추가
df_work[['lat', 'lon']] = df_work.apply(transform_coords, axis=1)

In [8]:
df_work[['lat', 'lon']].sample()

lat         lon
7027  37.549112  126.875791

In [9]:
# 서울시 중심 좌표
seoul_center = [37.5665, 126.9780]

# 지도 생성 (중심 좌표를 서울시 중심으로 설정)
m = folium.Map(location=seoul_center, zoom_start=12)

# 지도에 마커 추가
for _, row in df_work.iterrows():
    folium.Circle(
        location=(row['lat'], row['lon']),
        popup=row['구명'],
        radius=50,
        color='blue',
        fill=True,
        fill_color='blue',
        ).add_to(m)

# 지도 저장 또는 표시
m.save('map.html')
m